In [2]:
import pandas as pd
import os

In [3]:
DATA_DIR = "../data"
PROCESSED_DIR = "../processed/"
FACET_DIR = "for_sale_listings/"
FULL_DATA_DIR_PATH = os.path.join(DATA_DIR, FACET_DIR)
FULL_PROCESSED_DIR_PATH = os.path.join(PROCESSED_DIR, FACET_DIR)

In [7]:
# base cols RegionID,SizeRank,RegionName,RegionType,StateName

exclude_columns = [
    "RegionID",
    "SizeRank",
    "RegionName",
    "RegionType",
    "StateName",
    "Home Type",
]

batches = {"mlp": [], "new_listings": [], "new_pending": []}

for filename in os.listdir(FULL_DATA_DIR_PATH):
    if filename.endswith(".csv"):
        print("processing " + filename)
        cur_df = pd.read_csv(os.path.join(FULL_DATA_DIR_PATH, filename))

        # ignore monthly data for now since it is redundant
        if "monthly" in filename:
            continue

        if "sfrcondo" in filename:
            cur_df["Home Type"] = "all homes"
        elif "sfr" in filename:
            cur_df["Home Type"] = "SFR"
        elif "condo" in filename:
            cur_df["Home Type"] = "condo/co-op only"

        # Identify columns to pivot
        columns_to_pivot = [col for col in cur_df.columns if col not in exclude_columns]

        smoothed = "_sm_" in filename

        if "_mlp_" in filename:
            cur_df = pd.melt(
                cur_df,
                id_vars=exclude_columns,
                value_vars=columns_to_pivot,
                var_name="Date",
                value_name=(
                    "Median Listing Price"
                    if not smoothed
                    else "Median Listing Price (Smoothed)"
                ),
            )
            batches["mlp"].append(cur_df)

        elif "_new_listings_" in filename:
            cur_df = pd.melt(
                cur_df,
                id_vars=exclude_columns,
                value_vars=columns_to_pivot,
                var_name="Date",
                value_name=(
                    "New Listings" if not smoothed else "New Listings (Smoothed)"
                ),
            )
            batches["new_listings"].append(cur_df)

        elif "new_pending" in filename:
            cur_df = pd.melt(
                cur_df,
                id_vars=exclude_columns,
                value_vars=columns_to_pivot,
                var_name="Date",
                value_name="New Pending" if not smoothed else "New Pending (Smoothed)",
            )
            batches["new_pending"].append(cur_df)

matching_cols = [
    "RegionID",
    "Date",
    "SizeRank",
    "RegionName",
    "RegionType",
    "StateName",
    "Home Type",
]

combined_batches = [pd.concat(cur_batch) for cur_batch in batches.values()]

if len(combined_batches) > 0:
    combined_df = combined_batches[0]
    for batch in combined_batches[1:]:
        combined_df = pd.merge(
            combined_df,
            batch,
            on=matching_cols,
            how="outer",
        )


combined_df

processing Metro_new_pending_uc_sfrcondo_sm_month.csv
processing Metro_invt_fs_uc_sfrcondo_week.csv
processing Metro_mlp_uc_sfrcondo_week.csv
processing Metro_invt_fs_uc_sfr_month.csv
processing Metro_mlp_uc_sfr_sm_month.csv
processing Metro_new_pending_uc_sfrcondo_month.csv
processing Metro_mlp_uc_sfrcondo_sm_week.csv
processing Metro_invt_fs_uc_sfrcondo_month.csv
processing Metro_mlp_uc_sfr_sm_week.csv
processing Metro_mlp_uc_sfrcondo_month.csv
processing Metro_new_pending_uc_sfrcondo_sm_week.csv
processing Metro_invt_fs_uc_sfr_sm_week.csv
processing Metro_invt_fs_uc_sfr_sm_month.csv
processing Metro_mlp_uc_sfr_month.csv
processing Metro_new_listings_uc_sfrcondo_week.csv
processing Metro_mlp_uc_sfrcondo_sm_month.csv
processing Metro_invt_fs_uc_sfrcondo_sm_week.csv
processing Metro_new_listings_uc_sfrcondo_sm_week.csv
processing Metro_new_listings_uc_sfrcondo_month.csv
processing Metro_new_pending_uc_sfrcondo_week.csv
processing Metro_invt_fs_uc_sfr_week.csv
processing Metro_new_listi

RegionID  SizeRank     RegionName RegionType StateName  Home Type  \
0          102001         0  United States    country       NaN  all homes   
1          102001         0  United States    country       NaN        SFR   
2          102001         0  United States    country       NaN  all homes   
3          102001         0  United States    country       NaN        SFR   
4          102001         0  United States    country       NaN  all homes   
...           ...       ...            ...        ...       ...        ...   
2398144    845172       769   Winfield, KS        msa        KS  all homes   
2398145    845172       769   Winfield, KS        msa        KS        SFR   
2398146    845172       769   Winfield, KS        msa        KS        SFR   
2398147    845172       769   Winfield, KS        msa        KS  all homes   
2398148    845172       769   Winfield, KS        msa        KS  all homes   

               Date  Median Listing Price  Median Listing Price (Smoothed)  \
0        2018-01-06                   NaN                              NaN   
1        2018-01-13              259000.0                              NaN   
2        2018-01-13              259900.0                              NaN   
3        2018-01-20              259900.0                              NaN   
4        2018-01-20              259900.0                              NaN   
...             ...                   ...                              ...   
2398144  2023-12-31                   NaN                         136233.0   
2398145  2024-01-06                   NaN                         131088.0   
2398146  2024-01-06              135450.0                              NaN   
2398147  2024-01-06              128000.0                              NaN   
2398148  2024-01-06                   NaN                         121488.0   

         New Listings  New Listings (Smoothed)  New Pending (Smoothed)  \
0                 NaN                      NaN                     NaN   
1                 NaN                      NaN                     NaN   
2             71177.0                      NaN                     NaN   
3                 NaN                      NaN                     NaN   
4             72625.0                      NaN                     NaN   
...               ...                      ...                     ...   
2398144           NaN                     28.0                     NaN   
2398145           NaN                      NaN                     NaN   
2398146           NaN                      NaN                     NaN   
2398147           NaN                      NaN                     NaN   
2398148           NaN                      NaN                     NaN   

         New Pending  
0            24766.0  
1                NaN  
2            35229.0  
3                NaN  
4            38281.0  
...              ...  
2398144         24.0  
2398145          NaN  
2398146          NaN  
2398147          NaN  
2398148          NaN  

[2398149 rows x 13 columns]

In [6]:
final_df = combined_df
final_df = final_df.rename(
    columns={
        "RegionID": "Region ID",
        "SizeRank": "Size Rank",
        "RegionName": "Region",
        "RegionType": "Region Type",
        "StateName": "State",
    }
)

final_df

Region ID  Size Rank         Region Region Type State  Home Type  \
0           102001          0  United States     country   NaN  all homes   
1           102001          0  United States     country   NaN        SFR   
2           102001          0  United States     country   NaN  all homes   
3           102001          0  United States     country   NaN        SFR   
4           102001          0  United States     country   NaN  all homes   
...            ...        ...            ...         ...   ...        ...   
2398144     845172        769   Winfield, KS         msa    KS  all homes   
2398145     845172        769   Winfield, KS         msa    KS        SFR   
2398146     845172        769   Winfield, KS         msa    KS        SFR   
2398147     845172        769   Winfield, KS         msa    KS  all homes   
2398148     845172        769   Winfield, KS         msa    KS  all homes   

               Date  Median Listing Price  Median Listing Price (Smoothed)  \
0        2018-01-06                   NaN                              NaN   
1        2018-01-13              259000.0                              NaN   
2        2018-01-13              259900.0                              NaN   
3        2018-01-20              259900.0                              NaN   
4        2018-01-20              259900.0                              NaN   
...             ...                   ...                              ...   
2398144  2023-12-31                   NaN                         136233.0   
2398145  2024-01-06                   NaN                         131088.0   
2398146  2024-01-06              135450.0                              NaN   
2398147  2024-01-06              128000.0                              NaN   
2398148  2024-01-06                   NaN                         121488.0   

         New Listings  New Listings (Smoothed)  New Pending (Smoothed)  \
0                 NaN                      NaN                     NaN   
1                 NaN                      NaN                     NaN   
2             71177.0                      NaN                     NaN   
3                 NaN                      NaN                     NaN   
4             72625.0                      NaN                     NaN   
...               ...                      ...                     ...   
2398144           NaN                     28.0                     NaN   
2398145           NaN                      NaN                     NaN   
2398146           NaN                      NaN                     NaN   
2398147           NaN                      NaN                     NaN   
2398148           NaN                      NaN                     NaN   

         New Pending  
0            24766.0  
1                NaN  
2            35229.0  
3                NaN  
4            38281.0  
...              ...  
2398144         24.0  
2398145          NaN  
2398146          NaN  
2398147          NaN  
2398148          NaN  

[2398149 rows x 13 columns]

In [49]:
if not os.path.exists(FULL_PROCESSED_DIR_PATH):
    os.makedirs(FULL_PROCESSED_DIR_PATH)

final_df.to_json(FULL_PROCESSED_DIR_PATH + "final.jsonl", orient="records", lines=True)